In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, udf, regexp_extract, explode, lower, length, trim, when, regexp_replace, collect_list, struct, concat_ws
from pyspark.sql import functions as F

import sparknlp
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.linalg import Vectors
from pyspark.ml.functions import array_to_vector

import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt

In [0]:
spark = sparknlp.start()
clusters_pd = pd.read_csv('data/clustering_4options.csv')
requirements_clusters = spark.createDataFrame(clusters_pd)

cluster_titles_pd = pd.read_csv('data/Grouped_Clusters.csv')
final_clusters = spark.createDataFrame(cluster_titles_pd)

In [0]:
# Convert string columns to arrays

def to_float_array(embedding_str):
    return [float(x) for x in embedding_str.strip("[]").split(",")]
def to_int_array(embedding_str):
    return [int(x) for x in embedding_str.strip("[]").split(",")]
def to_string_array(embedding_str):
    return [x for x in embedding_str.strip("[]").split(",")]
    
to_float_array_udf = udf(to_float_array, ArrayType(FloatType()))
requirements_clusters = requirements_clusters.withColumn("Embeddings", to_float_array_udf(col("Embeddings_Model1"))).drop("Embeddings_Model1", "Embeddings_Model2")

to_int_array_udf = udf(to_int_array, ArrayType(IntegerType()))
to_string_array_udf = udf(to_string_array, ArrayType(StringType()))
final_clusters = final_clusters.withColumn("Clusters", to_int_array_udf(col("Clusters"))).withColumn("Job_Titles", to_string_array_udf(col("Job_Titles")))


# Map cluster numbers to cluster titles
cluster_mapping = final_clusters.select(explode("Clusters").alias("Cluster"), "Cluster_Title")
requirements_clusters_new = requirements_clusters.join(
    cluster_mapping,
    requirements_clusters["Cluster_DBSCAN_Model1"] == cluster_mapping["Cluster"],
    how="left"
).drop("Cluster")

requirements_clusters_new.display()

Title Company Full Job Description Search Word Description Description_English Requirements_Text Cluster_spark_KMeans_1 Cluster_spark_KMeans_2 Cluster_DBSCAN_Model1 Cluster_DBSCAN_Model2 Embeddings Cluster_Title Data Analytics Apple Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Opened URL: https://il.indeed.com/rc/clk?jk=0433bc7e45e694a3&bb=r6UIYw2mow7Pn8IzQwq2_7gXyX4L0a9oUPOLDIseoxAN8l0MRFFfCqpU6vSJRCmVlzxZCXcY6V-lzbB66NkEzDukGjQJgUJrBPff0HR1apFcJos6F0MbonwvLMjHhNz9&xkcb=SoDD67M33wH7H8WWaB0JbzkdCdPP&fccid=8e007f7a76f9cee5&vjs=3 data Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal

# Skill List

## N-grams

In [0]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [0]:
from pyspark.ml.feature import NGram, Tokenizer
from pyspark.ml import Pipeline
from nltk.corpus import stopwords

stop_words = set(stopwords.words('english'))
words_out = ['year', 'experience', 'degree', 'b.sc', 'bachelor', 'url', 'skill', 'bsc', 'salary', 'qualification']

tokenizer = Tokenizer(inputCol="Requirements_Text", outputCol="words")
tokenized = tokenizer.transform(requirements_clusters_new)
bigram = NGram(n=2, inputCol="words", outputCol="bigrams")
ngram_data = bigram.transform(tokenized)
trigram = NGram(n=3, inputCol="words", outputCol="trigrams")
ngram_data = trigram.transform(ngram_data)
quadrigram = NGram(n=4, inputCol="words", outputCol="quads")
ngram_data = quadrigram.transform(ngram_data)

# Function to clean individual tokens
def clean_tokens(token, ngram=False):
    tokens = token.split('/')
    tokens = [re.sub(r'[^a-zA-Z\+\-]', '', t).strip() for t in tokens if not any(w in t for w in words_out)]
    tokens = [t for t in tokens if t]  # Remove empty strings or tokens that are just spaces
    
    if ngram:
        return ' or '.join(tokens)
    tokens = [t for t in tokens if any(char.isalpha() for char in t)]  # Keep tokens with at least one letter
    return tokens

def clean_unigram(tokens):
    cleaned = []
    for token in tokens:
        for w in clean_tokens(token.lower()):
            if w in stop_words:
                continue
            cleaned.append(w)
    return cleaned

# Function to clean n-grams
def clean_ngram(ngrams, n=2):
    cleaned = []
    for x in ngrams:
        tokens = x.split()
        if not x or not tokens or len(tokens) < n or any(w in x.lower() for w in words_out):     # Accounted for in other columns
            continue
        # Remove if there are unwanted symbols - all n
        if any(sym in x for sym in ['_', '. ']) or x.count('"') % 2 == 1 or (x.count('(') + x.count(')')) % 2 == 1:
            continue
        # Remove if there are unwanted symbols - n = 2, 3
        if n <= 3 and (any(sym in x for sym in [', ', '- ', ' -', ' (']) or any(sym in tokens[0] for sym in [')'])):
            continue
        # Clean each token in the n-gram separately
        words = [clean_tokens(t.lower(), ngram=True) for t in tokens]
        words = [w for w in words if w]
        if len(words) < len(tokens) or (len(words) <= 2 and any(w in stop_words for w in words)) or (len(words) > 2 and (words[-1] in stop_words or words[0] in stop_words)):
            continue
        cleaned.append(' '.join(words))
    return cleaned

# Clean n-grams
clean_bigram_udf = udf(lambda bigram: clean_ngram(bigram, n=2), ArrayType(StringType()))
cleaned_ngram = ngram_data.withColumn("cleaned_bigrams", clean_bigram_udf(col("bigrams")))
clean_trigram_udf = udf(lambda trigram: clean_ngram(trigram, n=3), ArrayType(StringType()))
cleaned_ngram = cleaned_ngram.withColumn("cleaned_trigrams", clean_trigram_udf(col("trigrams")))
clean_quadrigram_udf = udf(lambda quad: clean_ngram(quad, n=4), ArrayType(StringType()))
cleaned_ngram = cleaned_ngram.withColumn("cleaned_quads", clean_quadrigram_udf(col("quads")))

# Clean individual words
cleaned_tokens_udf = udf(clean_unigram, ArrayType(StringType()))
cleaned_ngram = cleaned_ngram.withColumn("cleaned_unigrams", cleaned_tokens_udf(col("words")))


# cleaned_ngram.select("Requirements_Text", "cleaned_unigrams", "cleaned_bigrams", "cleaned_trigrams", "cleaned_quads").limit(10).display()
cleaned_ngram.select("Requirements_Text", "cleaned_trigrams", "cleaned_quads").limit(50).display()

Requirements_Text cleaned_trigrams cleaned_quads +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) List(ability to lead, lead data investigations, investigations and analysis, projects with ambiguous, ambiguous requirements advanced, requirements advanced statistic, statistic and modeling, visualizing and presenting, analyses in tools, tools like jupyter, jupyter and tableau, programming in python, professional setting familiarity, familiarity with distributed, databases and sql, sql highly organized, passionate about achieving, achieving results curious, analytical and problem, familiarity with distributed) List(ability to lead data, data investigations and analysis, investigations and analysis projects, analysis projects with ambiguous, projects with ambiguous requirements, ambiguous requirements advanced statistic, advanced statistic and modeling, statistic and modeling knowledge, visualizing and presenting analyses, presenting analyses in tools, analyses in tools like, like jupyter and tableau, python in a professional, setting familiarity with distributed, familiarity with distributed computation, computation storage and workflow, storage and workflow management, splunk spark kubernetes kafka, spark kubernetes kafka hadoop, kubernetes kafka hadoop mapreduce, kafka hadoop mapreduce airflow, relational databases and sql, databases and sql highly, sql highly organized creative, highly organized creative motivated, creative motivated and passionate, passionate about achieving results, curious and have excellent, excellent analytical and problem, analytical and problem solving, written verbal and data, verbal and data communication, familiarity with distributed computation, computation storage and workflow, storage and workflow management, splunk spark kubernetes kafka, spark kubernetes kafka hadoop, kubernetes kafka hadoop mapreduce, kafka hadoop mapreduce airflow) into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker List(designs and tasks, production troubleshooting requirements, troubleshooting requirements -, developing data-oriented products, data-oriented products preferably, products preferably using, preferably using python or java, data processing fw, developing microservices-based architecture, working in container-based, container-based environments using, environments using tools, agile environment nice, machine learning fws, redhat openshift dev, openshift dev environment, dev environment know

In [0]:
from pyspark.sql.functions import collect_list, array_distinct
from collections import Counter

# Collect cleaned n-grams per cluster
clustered_data = cleaned_ngram.groupBy("Cluster_Title").agg(
    collect_list("cleaned_unigrams").alias("unigrams"),
    collect_list("cleaned_bigrams").alias("bigrams"),
    collect_list("cleaned_trigrams").alias("trigrams"),
    collect_list("cleaned_quads").alias("quads")
)

# Create bag of words for each cluster
def create_cluster_bag(unigrams, bigrams, trigrams, quads):
    # all_words = set(unigrams + bigrams + trigrams + quads)
    all_ngrams = [word for sublist in unigrams + bigrams + trigrams + quads for word in sublist]
    ngram_counts = Counter(all_ngrams)
    filtered_ngrams = [ngram for ngram, count in ngram_counts.items() if count > 15]
    return filtered_ngrams

cluster_bag_udf = udf(create_cluster_bag, ArrayType(StringType()))
clustered_data = clustered_data.withColumn("skills_bag", cluster_bag_udf(
    col("unigrams"), col("bigrams"), col("trigrams"), col("quads")
))

clustered_data.select("Cluster_Title", "skills_bag").limit(10).display()


Cluster_Title skills_bag data scientist List(ability, lead, data, analysis, projects, requirements, advanced, modeling, knowledge, tools, like, tableau, programming, python, professional, setting, familiarity, distributed, computation, storage, workflow, management, eg, splunk, spark, kubernetes, kafka, hadoop, mapreduce, airflow, etc, relational, databases, sql, highly, organized, creative, motivated, passionate, results, curious, excellent, analytical, problem, written, verbal, communication, masters, computer, science, preferred, industrial, engineering, analytics, statistics, related, field, proficiency, strong, focus, libraries, manipulation, querying, managing, large, datasets, bi, create, dashboards, reports, english, analyst, advantage, snowflake, aws, web, product, concepts, including, ai, language, models, llms, understanding, trends, patterns, actionable, insights, provide, recommendations, based, support, business, decisions, drive, develop, using, platforms, optimize, pipelines, collaborate, cross-functional, teams, data-driven, decision-making, relevant, technical, equivalent, responsibility, working, include, roles, scientist, engineer, similar, minimum, phd, etl, least, one, c++, c, scala, meta, technologies, help, people, connect, find, communities, grow, businesses, instagram, around, world, beyond, screens, build, social, technology, careers, building, us, future, take, digital, connection, makes, possible, even, physics, individual, compensation, location, details, posting, base, rate, annual, bonus, equity, applicable, addition, offers, benefits, learn, mathematics, cloud, google, azure, previous, security, industry, join, securing, worlds, rubrik, nyse, rbrk, mission, secure, zero, trust, organizations, achieve, resilience, cyberattacks, malicious, insiders, operational, disruptions, powered, machine, learning, secures, across, enterprise, saas, applications, uphold, integrity, deliver, availability, withstands, adverse, conditions, continuously, monitor, risks, threats, restore, infrastructure, attacked, linkedin, x, formerly, twitter, rubrikcom, diversity, inclusion, committed, sustaining, culture, backgrounds, valued, know, belong, believe, succeed, rubriks, goal, hire, promote, best, person, job, matter, background, correcting, systemic, processes, cultural, norms, prevented, equal, representation, means, review, current, efforts, intent, offer, fair, hiring, promotion, opportunities, historically, underrepresented, strive, company, employees, feel, bring, authentic, selves, work, successful, dei, strategy, focuses, three, core, areas, diverse, provides, equitable, access, growth, success, globally, inclusive, environment, authenticity, thrives, expand, commitment, within, walls, invest, generations, talent, innovation, clients, opportunity, employer, veterans, disabled, qualified, applicants, receive, consideration, employment, without, regard, race, color, religion, sex, sexual, orientation, gender, identity, national, origin, protected, veteran, status, discriminated, basis, disability, eeo, age, genetics, federal, law, complies, state, local, laws, governing, nondiscrimination, every, facilities, policy, applies, terms, recruiting, placement, termination, layoff, recall, transfer, leaves, absence, training, requires, employers, reasonable, accommodation, individuals, disabilities, please, contact, hrrubrikcom, require, apply, perform, examples, making, change, application, process, procedures, providing, documents, alternate, format, sign, interpreter, specialized, equipment, development, operating, tabular, mining, privitar, dataiku, tables, healthcare, mandatory, free, text, hebrew, significant, researchers, academia, first, applied, math, algorithm, proven, algorithms, supervised, unsupervised, optimization, following, r, matlab, driven, quick, learner, big, processing, nosql, name, number, required, upload, share, let, friends, graduate, must, exceptional, high, attention, detail, multiple, in

In [0]:
# Create bag of words for all the data
skills_bag_lists = clustered_data.select("skills_bag").rdd.flatMap(lambda row: row.skills_bag).collect()

# Flatten the list of lists and convert to a set for unique words
unique_skills_set = set(skills_bag_lists)

print(len(unique_skills_set))

print(unique_skills_set)

1700
{'learning frameworks', 'problems for customers improvise', 'future generations', 'passionate', 'job or to perform', 'problem', 'receive', 'sick', 'quickly', 'page', 'data and draw insights', 'secure', 'statistical computer languages python', 'believe', 'gan', 'supervised and unsupervised', 'documents in an alternate', 'withstands adverse conditions continuously', 'relational databases', 'talent', 'competencies able', 'querying', 'lead projects independently', 'federal law requires employers', 'technical solutions', 'application', 'align', 'termination layoff recall transfer', 'python to manipulate data', 'processing', 'variety', 'computation', 'field', 'rubrik', 'dei strategy focuses', 'tools including mlflow', 'ml', 'information presentation - smsedgecom or presentation', 'text mining', 'desirable', 'li-hybrid', 'secures data across enterprise', 'ability to execute', 'insights', 'local laws governing nondiscrimination', 'areas', 'initiatives', 'clear and concise', 'sql and pytho

## NER

In [0]:
%pip install spacy
!python -m spacy download en_core_web_sm

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 82.5 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.2.1 -> 25.0
[notice] To update, run: pip install --upgrade pip
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [0]:
import spacy

nlp = spacy.load("en_core_web_sm")

def extract_skills(text):
    doc = nlp(text)
    skills = [ent.text for ent in doc.ents if ent.label_ in ['PRODUCT', 'ORG', 'SKILL']]
    return skills

extract_skills_udf = udf(lambda text: extract_skills(text), ArrayType(StringType()))
ner_df = requirements_clusters_new.withColumn("extracted_skills", extract_skills_udf(col("Requirements_Text")))

ner_df.select("Requirements_Text", "extracted_skills").limit(10).display()

Requirements_Text extracted_skills +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) List(Hadoop, MapReduce, AirFlow, SQL Highly, Bachelor, Hadoop, MapReduce, AirFlow) into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker List(Python/Java Experience, Spark, Hadoop, SKLearn, Tensorflow, RedHat) A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. List(SQL, MATLAB) B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Freshly made coffee, shakes, and afternoon salads by our in-house barista. - Health & Wellness: Full health insurance coverage for your peace of mind. - Growth Opportunities: Learning and training programs to enhance your personal and professional skills. - Vibrant Culture: Happy hours, team events, and plenty of opportunities to connect with colleagues. Join us and experience a workplace where your well-being, growth, and enjoyment come first! List(B.A, SQL, Strong Excel /, Google Sheets, Desired Marketing, KPI, - Health 

In [0]:
from transformers import pipeline

# Load a pretrained pipeline for token classification
ner_pipeline = pipeline("ner", model="dslim/bert-base-NER")

# Function to extract skills using the NER pipeline
def extract_skills_with_ner(text):
    ner_results = ner_pipeline(text)
    skills = [res['word'] for res in ner_results if res['entity'] in ['B-SKILL', 'I-SKILL']]
    return skills

# Apply the function to your data
extract_skills_udf = udf(lambda text: extract_skills_with_ner(text), ArrayType(StringType()))
ner_df = requirements_clusters_new.withColumn("extracted_skills", extract_skills_udf(col("Requirements_Text")))

ner_df.select("Requirements_Text", "extracted_skills").limit(10).display()

2025-02-04 11:10:11.771057: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-02-04 11:10:11.857913: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-02-04 11:10:12.219574: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-02-04 11:10:16.528343: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


config.json:   0%|          | 0.00/829 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/433M [00:00<?, ?B/s]

Some weights of the model checkpoint at dslim/bert-base-NER were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


tokenizer_config.json:   0%|          | 0.00/59.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.00 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Requirements_Text extracted_skills +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) List() into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker List() A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. List() B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Freshly made coffee, shakes, and afternoon salads by our in-house barista. - Health & Wellness: Full health insurance coverage for your peace of mind. - Growth Opportunities: Learning and training programs to enhance your personal and professional skills. - Vibrant Culture: Happy hours, team events, and plenty of opportunities to connect with colleagues. Join us and experience a workplace where your well-being, growth, and enjoyment come first! List() B.Sc in Industrial Engineering, Data Analytics, Statistics, or a related field. Proficiency in Python, with a strong focus on libraries like Pandas for data manipulation. Solid knowledge of SQL for querying and managing large

## Q\A

In [0]:
from transformers import pipeline

qa_pipeline = pipeline("question-answering", model="distilbert-base-cased-distilled-squad")

q = "What are all the job requirements and qualifications?"

def extract_skills_from_text(text):
    answer = qa_pipeline(question=q, context=text)
    a = answer['answer']
    return a

def extract_skill_list(a):
    if a:
        a = a.split(", ")
        if a[-1].startswith("and"):
            a[-1] = a[-1][4:]
    return a

extract_skills_udf = udf(extract_skills_from_text, StringType())
extract_skill_list_udf = udf(extract_skill_list, ArrayType(StringType()))

cleaned_ngram_with_skills = cleaned_ngram.withColumn("extracted_skills_qa", extract_skills_udf(col("Requirements_Text")))
cleaned_ngram_with_skills = cleaned_ngram_with_skills.withColumn("skill_list", extract_skill_list_udf(col("extracted_skills_qa")))

cleaned_ngram_with_skills.select("Requirements_Text", "extracted_skills_qa", "skill_list").display()


config.json:   0%|          | 0.00/473 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/261M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

Requirements_Text extracted_skills_qa skill_list +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) distributed computation, storage, and workflow management List(distributed computation, storage, workflow management) into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker actionable designs List(actionable designs) A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. Good written and verbal skills List(Good written and verbal skills) B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Freshly made coffee, shakes, and afternoon salads by our in-house barista. - Health & Wellness: Full health insurance coverage for your peace of mind. - Growth Opportunities: Learning and training programs to enhance your personal and professional skills. - Vibrant Culture: Happy hours, team events, and plenty of opportunities to connect with colleagues. Join us and experience a workplace where your well-being, growth, and enjoyment come first! Growth Op

## Semantic Search

In [0]:
skills_bow = list(unique_skills_set)

In [0]:
from sentence_transformers import SentenceTransformer, util

model = SentenceTransformer('all-MiniLM-L6-v2')

skills_embeddings = model.encode(skills_bow, convert_to_tensor=True)

def extract_skills_from_text2(text):
    # Encode the job description (context)
    context_embedding = model.encode(text, convert_to_tensor=True)
    
    # Perform semantic search to find the most relevant skills
    results = util.semantic_search(context_embedding, skills_embeddings, top_k=5)
    
    # Extract the top skills based on the semantic search results
    top_skills = [skills_bow[result['corpus_id']] for result in results[0]]
    
    return ", ".join(top_skills)

def extract_skill_list2(a):
    if a:
        a = a.split(", ")
    return a

extract_skills_udf2 = udf(extract_skills_from_text2, StringType())
extract_skill_list_udf2 = udf(extract_skill_list2, ArrayType(StringType()))

cleaned_ngram_with_skills2 = cleaned_ngram.withColumn("extracted_skills_semantic", extract_skills_udf2(col("Requirements_Text")))
cleaned_ngram_with_skills2 = cleaned_ngram_with_skills2.withColumn("skill_list", extract_skill_list_udf2(col("extracted_skills_semantic")))

cleaned_ngram_with_skills2.select("Requirements_Text", "extracted_skills_semantic", "skill_list").display()


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

/databricks/python/lib/python3.11/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Requirements_Text extracted_skills_semantic skill_list +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) data engineer, data scientist, data science computer science, proficiency in programming, computer science data science List(data engineer, data scientist, data science computer science, proficiency in programming, computer science data science) into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker devops, devops practices, management tools including mlflow, software development, spark kubernetes kafka hadoop List(devops, devops practices, management tools including mlflow, software development, spark kubernetes kafka hadoop) A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. title data engineer, data scientist, data engineer, title data scientist, data science or another List(title data engineer, data scientist, data engineer, title data scientist, data science or another) B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Fr

In [0]:
from pyspark.sql.functions import collect_list, struct, map_from_entries, count

exploded_skills = cleaned_ngram_with_skills2.withColumn("skill", explode(col("skill_list")))

# Count the occurrences of each skill in each cluster
skill_counts = exploded_skills.groupBy("Cluster_Title", "skill").agg(
    count("Requirements_Text").alias("skill_count")
)

# Get the total number of jobs per cluster
cluster_sizes = cleaned_ngram_with_skills2.groupBy("Cluster_Title").agg(
    count("Requirements_Text").alias("cluster_size")
)

skill_stats = skill_counts.join(cluster_sizes, "Cluster_Title")

# Calculate the percentage of jobs requiring each skill
skill_stats = skill_stats.withColumn(
    "percentage", (col("skill_count") / col("cluster_size")) * 100
)

# Create a dictionary for skills and their percentages
skill_dict_percent = skill_stats.groupBy("Cluster_Title").agg(
    map_from_entries(collect_list(struct(col("skill"), col("percentage")))).alias("skills_statistics")
)

skill_dict_percent.select("Cluster_Title", "skills_statistics").display()


Cluster_Title skills_statistics data scientist Map(data scientist -> 71.8232044198895, kubernetes kafka hadoop mapreduce -> 4.143646408839778, data analyst -> 22.65193370165746, devops -> 2.7624309392265194, hiring -> 3.314917127071823, data security we help -> 5.524861878453039, familiarity with cloud platforms -> 3.591160220994475, cloud platforms -> 0.8287292817679558, data pipelines -> 1.3812154696132597, inclusive environment -> 0.5524861878453038, computer science applied math -> 3.314917127071823, data engineer company -> 18.784530386740332, career -> 1.3812154696132597, data infrastructure -> 0.8287292817679558, recruiting hiring placement promotion -> 0.5524861878453038, full-time -> 1.1049723756906076, data roles -> 1.3812154696132597, qualified applicants -> 1.3812154696132597, tabular data mining -> 5.524861878453039, data tools -> 4.143646408839778, applicants for employment -> 1.6574585635359116, google cloud or azure -> 0.8287292817679558, core competencies able -> 0.8287292817679558, familiarity with cloud -> 1.3812154696132597, qualified individuals with disabilities -> 0.2762430939226519, thrives and people -> 0.5524861878453038, provides equal employment opportunities -> 2.209944751381215, securing the worlds data -> 2.209944751381215, computer science data science -> 2.209944751381215, requirements ability -> 0.8287292817679558, competencies able -> 0.8287292817679558, build a diverse company -> 0.8287292817679558, data science computer science -> 17.403314917127073, equal employment opportunities -> 1.6574585635359116, zero trust data security -> 3.314917127071823, compensation opportunities -> 1.6574585635359116, title data engineer -> 12.154696132596685, software development -> 3.591160220994475, data science toolkits -> 3.314917127071823, equal employment -> 1.6574585635359116, free text mining -> 3.314917127071823, engineering data science bi -> 11.049723756906078, equal opportunity employer -> 1.6574585635359116, data analyst company -> 11.049723756906078, title data scientist company -> 2.209944751381215, employment opportunities -> 2.7624309392265194, pyspark -> 2.7624309392265194, equal employment opportunities eeo -> 1.3812154696132597, spark kubernetes kafka hadoop -> 4.143646408839778, meta -> 3.0386740331491713, title data scientist -> 18.784530386740332, requirements ability to learn -> 11.878453038674033, cloud and saas applications -> 0.8287292817679558, hadoop -> 4.143646408839778, rubrik security cloud -> 5.524861878453039, spark -> 2.7624309392265194, competencies able to solve -> 7.734806629834254, build a diverse -> 0.2762430939226519, competencies -> 5.801104972375691, requirements -> 4.972375690607735, familiarity with cloud-based -> 3.0386740331491713, core competencies -> 0.8287292817679558, tech -> 3.0386740331491713, commitment to diversity -> 0.5524861878453038, analytics data engineering data -> 0.5524861878453038, data scientist company -> 2.209944751381215, data mining -> 3.314917127071823, requirements into technical -> 4.696132596685083, computer science -> 6.629834254143646, analytics -> 1.9337016574585635, diverse company -> 0.5524861878453038, proficiency in programming languages -> 3.591160220994475, computer science applied -> 5.248618784530387, data science or another -> 29.2817679558011, proficiency in python -> 1.3812154696132597, using data science -> 2.209944751381215, careers -> 9.116022099447514, company build a diverse -> 1.3812154696132597, diverse company that provides -> 0.5524861878453038, rubrik security cloud powered -> 5.524861878453039, proficiency in programming -> 15.745856353591158, data engineer -> 69.61325966850829, data science -> 2.209944751381215, commitment to diversity equity -> 0.8287292817679558, security cloud -> 5.524861878453039) etl developer Map(oracle -> 100.0, data across enterprise -> 100.0, data engineer company -> 100.0, knowledge of sql -> 100.0, data engineer -> 100.0) manager sem Map(qualified individuals -> 100.0, hire and promo